**CREATE SCHEMA POCCO**

In [4]:
CREATE SCHEMA STAGE_henrique_mesquita


Commands completed successfully.

Total execution time: 00:00:00.129

In [6]:
CREATE SCHEMA DW_henrique_mesquita

: Msg 2714, Level 16, State 6, Line 1
There is already an object named 'DW_henrique_mesquita' in the database.

: Msg 2759, Level 16, State 0, Line 1
CREATE SCHEMA failed due to previous errors.

Total execution time: 00:00:00.132

**CREATE TABLES - Criação das tabelas Fato e Dimensões**

In [3]:
-- TABELA DIMENSÃO -> SALES CHANNEL (DIM.SALES_CHANNEL)
CREATE TABLE [DW_henrique_mesquita].[DIM_SALES_CHANNEL](
    ID_channel INT PRIMARY KEY IDENTITY(1,1),
    sales_channel VARCHAR(40) NOT NULL
);

-- TABELA DIMENSÃO -> REGION (DIM.REGION)
CREATE TABLE [DW_henrique_mesquita].[DIM_REGION](
    ID_region INT PRIMARY KEY IDENTITY(1,1),
    region VARCHAR(40) NOT NULL
);

-- TABELA DIMENSÃO -> COUNTRY (DIM.COUNTRY)
CREATE TABLE [DW_henrique_mesquita].[DIM_COUNTRY](
    ID_country INT PRIMARY KEY IDENTITY(1,1),
    country VARCHAR(40) NOT NULL
);

--- TABELA FATOS -> SALES (FATO.SALES)
CREATE TABLE [DW_henrique_mesquita].[FATO_SALES](
    ID_order INT PRIMARY KEY,
    order_date DATE,
    ship_date DATE,
    item_type VARCHAR(40),
    units_sold INT,
    total_revenue DECIMAL(14,2),
    total_cost DECIMAL(14,2),
    total_profit DECIMAL(14,2),
    channel INT FOREIGN KEY REFERENCES DW_henrique_mesquita.DIM_SALES_CHANNEL(ID_channel),
    region INT FOREIGN KEY REFERENCES DW_henrique_mesquita.DIM_REGION(ID_region),
    country INT FOREIGN KEY REFERENCES DW_henrique_mesquita.DIM_COUNTRY(ID_country)
);

Commands completed successfully.

Total execution time: 00:00:00.170

**TESTE DE EXECUÇÃO**

In [13]:
EXECUTE DW_henrique_mesquita.PerformedTables

(0 rows affected)

(2 rows affected)

(7 rows affected)

(185 rows affected)

(2 rows affected)

(7 rows affected)

(185 rows affected)

(10000 rows affected)

Total execution time: 00:00:00.942

**CREATE PROCEDURE - Criando a procedure para tratamento dos dados e população do Data Warehouse**

In [11]:
CREATE PROCEDURE [DW_henrique_mesquita].[PerformedTables] AS
BEGIN -- Tratamento de erros > Consultando tabela Stage e verificando se ela está devidamente populada
    DECLARE @SizeStageTable INT;
    SELECT @SizeStageTable = count(*) from STAGE_henrique_mesquita.orders; 
IF @SizeStageTable = 0
    BEGIN 
        SELECT 'A tabela Stage está vazia! Execução cancelada!' as mensagem;
    END
ELSE
    BEGIN -- Atenção na ordem de declaração
        DELETE FROM DW_henrique_mesquita.FATO_SALES
        DELETE FROM DW_henrique_mesquita.DIM_SALES_CHANNEL
        DELETE FROM DW_henrique_mesquita.DIM_REGION
        DELETE FROM DW_henrique_mesquita.DIM_COUNTRY

        INSERT INTO DW_henrique_mesquita.DIM_SALES_CHANNEL (sales_channel)
        SELECT [Sales Channel]
        FROM STAGE_henrique_mesquita.orders
        GROUP BY [Sales Channel]
        ORDER BY [Sales Channel]

        INSERT INTO DW_henrique_mesquita.DIM_REGION (region)
        SELECT [Region]
        FROM STAGE_henrique_mesquita.orders
        GROUP BY [Region]
        ORDER BY [Region]

        INSERT INTO DW_henrique_mesquita.DIM_COUNTRY (country)
        SELECT [Country]
        FROM STAGE_henrique_mesquita.orders
        GROUP BY [Country]
        ORDER BY [Country]
-- Atenção na ordem de declaração
        INSERT INTO DW_henrique_mesquita.FATO_SALES
            (ID_order, item_type, order_date, ship_date, units_sold, total_revenue, total_cost, total_profit, channel, region, country)
        SELECT 
            st.[Order ID], st.[Item Type], CONVERT(DATE, REPLACE(st.[Order Date], '/', '-'),103),
            CONVERT(DATE, REPLACE(st.[Ship Date], '/', '-'),103), st.[Units Sold],
            REPLACE(st.[Total Revenue], ',', '.'), REPLACE(st.[Total Cost], ',', '.'), REPLACE(st.[Total Profit], ',', '.'),
            sc.ID_channel, rg.ID_region, ct.ID_country
        FROM STAGE_henrique_mesquita.orders st
        -- Atenção na ordem de declaração
        INNER JOIN DW_henrique_mesquita.DIM_SALES_CHANNEL sc ON st.[Sales Channel] = sc.sales_channel
        INNER JOIN DW_henrique_mesquita.DIM_REGION rg ON st.[Region] = rg.region
        INNER JOIN DW_henrique_mesquita.DIM_COUNTRY ct ON st.[Country] = ct.country
    END
END;
GO

Commands completed successfully.

Total execution time: 00:00:00.129

**TESTE DE EXECUÇÃO - Tabela Fato**

In [14]:
select * from DW_henrique_mesquita.FATO_SALES

(10000 rows affected)

Displaying Top 5000 rows.

Total execution time: 00:00:01.820

ID_order order_date ship_date item_type units_sold total_revenue total_cost total_profit channel region country 100089156 2013-09-04 2013-09-04 Cereal 7460 1534522,00 873640,60 660881,40 8 26 600 100168120 2012-08-07 2012-08-21 Fruits 828 7725,24 5729,76 1995,48 7 28 618 100200736 2011-05-02 2011-06-11 Snacks 479 73085,82 46673,76 26412,06 8 25 608 100315320 2016-08-24 2016-10-12 Cosmetics 4387 1917996,40 1155228,71 762767,69 7 23 728 100435912 2014-07-21 2014-09-08 Snacks 73 11138,34 7113,12 4025,22 7 24 597 100598990 2015-10-16 2015-11-10 Household 8332 5568025,64 4187163,28 1380862,36 8 25 683 100621736 2017-06-30 2017-08-18 Personal Care 5062 413717,26 286863,54 126853,72 8 25 595 100674521 2012-06-15 2012-07-08 Clothes 683 74638,24 24478,72 50159,52 7 23 656 100810134 2010-10-10 2010-11-02 Personal Care 814 66528,22 46129,38 20398,84 7 28 739 100813996 2015-03-18 2015-04-21 Beverages 1957 92859,65 62213,03 30646,62 7 28 560 100913560 2012-07-14 2012-08-26 Cosmetics 1420 620824,00 373928,60 246895,40 8 23 656 100935447 2017-06-19 2017-07-14 Vegetables 7897 1216611,82 718074,21 498537,61 7 27 615 100990378 2015-09-24 2015-10-22 Office Supplies 4152 2703823,92 2179633,92 524190,00 7 25 609 101056468 2017-07-18 2017-08-07 Vegetables 3709 571408,54 337259,37 234149,17 8 28 618 101077067 2015-12-13 2015-12-28 Office Supplies 9805 6385114,05 5147232,80 1237881,25 7 25 676 101141870 2011-03-29 2011-04-18 Cosmetics 8982 3926930,40 2365230,06 1561700,34 8 23 671 101274907 2011-08-26 2011-10-11 Household 8350 5580054,50 4196209,00 1383845,50 8 22 666 101289498 2017-06-17 2017-06-17 Office Supplies 2668 1737428,28 1400593,28 336835,00 8 28 658 101455152 2016-08-08 2016-08-09 Meat 1689 712572,21 615961,41 96610,80 8 25 736 101491630 2012-03-13 2012-04-20 Meat 2483 1047552,87 905525,27 142027,60 7 28 695 101580035 2013-07-18 2013-07-25 Beverages 8645 410205,25 274824,55 135380,70 8 25 730 101696765 2014-08-04 2014-09-19 Cosmetics 3188 1393793,60 839496,04 554297,56 8 25 612 101813924 2010-03-28 2010-04-26 Clothes 7857 858612,96 281594,88 577018,08 8 28 674 101823794 2014-11-02 2014-12-03 Office Supplies 778 506641,38 408418,88 98222,50 8 27 659 101836240 2017-05-05 2017-05-12 Vegetables 4461 687261,66 405638,73 281622,93 8 22 652 101844823 2015-06-01 2015-06-23 Snacks 7001 1068212,58 682177,44 386035,14 8 28 697 101917779 2014-03-05 2014-04-20 Clothes 8590 938715,20 307865,60 630849,60 7 25 714 101929795 2014-07-04 2014-07-30 Fruits 2146 20022,18 14850,32 5171,86 7 25 647 101939666 2011-07-13 2011-08-09 Beverages 5067 240429,15 161079,93 79349,22 7 22 701 102014338 2011-06-03 2011-07-07 Vegetables 7165 1103839,90 651513,45 452326,45 8 25 590 102073132 2014-02-12 2014-04-02 Snacks 4563 696222,54 444618,72 251603,82 7 28 708 102293288 2016-12-03 2016-12-09 Household 9712 6490238,24 4880668,48 1609569,76 7 28 605 102362811 2013-06-04 2013-06-19 Personal Care 285 23293,05 16150,95 7142,10 8 25 564 102393281 2016-06-05 2016-06-16 Fruits 9302 86787,66 64369,84 22417,82 8 28 572 102554643 2016-07-14 2016-07-18 Personal Care 7053 576441,69 399693,51 176748,18 8 23 704 102709996 2016-06-23 2016-07-01 Household 3025 2021516,75 1520183,50 501333,25 7 25 609 102760636 2015-09-15 2015-09-19 Baby Food 8011 2045048,08 1277113,62 767934,46 7 28 613 102914273 2014-07-09 2014-08-02 Personal Care 3475 284011,75 196928,25 87083,50 8 24 588 102957618 2014-08-18 2014-09-30 Meat 6302 2658750,78 2298276,38 360474,40 8 22 719 103000533 2012-07-24 2012-08-09 Cereal 9001 1851505,70 1054107,11 797398,59 7 22 632 103129708 2016-02-11 2016-03-12 Fruits 7227 67427,91 50010,84 17417,07 7 25 649 103256738 2016-05-11 2016-05-26 Meat 4818 2032666,02 1757076,42 275589,60 7 24 616 103342139 2010-01-20 2010-02-04 Vegetables 90 13865,40 8183,70 5681,70 8 28 644 103354156 2010-05-20 2010-07-05 Snacks 3646 556306,68 355266,24 201040,44 8 28 579 103417670 2014-04-17 2014-04-30 Meat 2442 1030255,38 890572,98 139682,40 7 25 559 103449857 2010-11-07 2010-12-20 Household 1966 1313